# Import

In [26]:
import numpy as np
import pandas as pd
import hvplot.pandas
import panel as pn
import param
import datetime as dt
import holoviews as hv
import requests
import dateutil.parser
import inspect
from datashader.colors import Sets1to3
from holoviews.operation.datashader import datashade
import datashader as ds
import intake
import os
#pn.extension('vtk')


# Lecture

In [37]:
# http://archive.ics.uci.edu/ml/datasets/Occupancy+Detection+
from zipfile import ZipFile
import urllib.request

filename ='http://archive.ics.uci.edu/ml/machine-learning-databases/00357/occupancy_data.zip'
to_filename = "../data/occupancy_data.zip"

if not os.path.isfile(to_filename):
    print('Download')
    urllib.request.urlretrieve(filename, to_filename)

zip_file = ZipFile(to_filename)
dfs = {
    text_file.filename: pd.read_csv(zip_file.open(text_file.filename))
       for text_file in zip_file.infolist()
       if text_file.filename.endswith('.csv') or text_file.filename.endswith('.txt')
}


In [60]:
df = dfs['datatest2.txt']
df.date = pd.to_datetime(df.date)
df.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 9752 entries, 1 to 9752
Data columns (total 7 columns):
date             9752 non-null datetime64[ns]
Temperature      9752 non-null float64
Humidity         9752 non-null float64
Light            9752 non-null float64
CO2              9752 non-null float64
HumidityRatio    9752 non-null float64
Occupancy        9752 non-null int64
dtypes: datetime64[ns](1), float64(5), int64(1)
memory usage: 609.5 KB


In [61]:
objects = {
    'x':list(df.columns), 
    'y':list(df.columns),
}
defaults = {
    'x':df.columns[0], 
    'y':[list(df.columns)[1]],
}

# Création class graph

In [62]:
def get_args(type_method):
    import re
    main_args = [arg for arg in inspect.getfullargspec(type_method).args if arg != 'self']
    all_args = {}

    regex_func = r"hvplot\.\w+\([\w+=, ]+\)"
    test_str =  inspect.getdoc(type_method)
    func_search = re.search(regex_func, test_str, re.IGNORECASE)
    if func_search:
        function = func_search.group(0)
        
        regex = r"([a-zA-z]+)=[a-zA-z]+"
        matches = re.finditer(regex, function, re.MULTILINE)
        
        for matchNum, match in enumerate(matches, start=1):
            key, val = match.group().split('=')
            all_args[key] = val
    return main_args, [arg for arg in all_args.keys() if arg not in main_args]

# Constuction Class Options
https://github.com/pyviz/hvplot/blob/master/hvplot/converter.py
https://github.com/pyviz/hvplot/blob/c092179e9c0948f0da1ee554d8af79c9261f045c/hvplot/__init__.py

In [63]:
# holoviewConverterProperties = inspect.getmembers(hvplot.HoloViewsConverter, lambda a:not(inspect.isroutine(a)))
hvConverterClass = hvplot.HoloViewsConverter

_gridded_types = hvConverterClass._gridded_types

_geom_types = hvConverterClass._geom_types

# _geo_types = hvConverterClass._geo_types

_stats_types = hvConverterClass._stats_types

_data_options = hvConverterClass._data_options

#_geo_options = hvConverterClass._geo_options

_axis_options = hvConverterClass._axis_options

_style_options = hvConverterClass._style_options

_op_options = hvConverterClass._op_options

_kind_options = hvConverterClass._kind_options

_kind_mapping = hvConverterClass._kind_mapping

_colorbar_types = hvConverterClass._colorbar_types

_legend_positions = hvConverterClass._legend_positions

# _default_plot_opts = hvConverterClass._default_plot_opts

# _default_cmaps = hvConverterClass._default_cmaps


# Default mapping

In [64]:
## Map
map_type_to_widget = {
    'C':'param.ObjectSelector(default="yellow", objects=["red","yellow","green"])',
    'c':'param.ObjectSelector(default="yellow", objects=["red","yellow","green"])',
    'text':'param.ObjectSelector(default="yellow", objects=["red","yellow","green"])',
    'bands':'param.ObjectSelector(default="yellow", objects=["red","yellow","green"])',
    'x':'param.ObjectSelector(default="yellow", objects=["red","yellow","green"])',
    'y':'param.ListSelector(default=["yellow"], objects=["red","yellow","green"])',
    'y2':'param.ObjectSelector(default="yellow", objects=["red","yellow","green"])',
    'by':'param.ObjectSelector(default="yellow", objects=["red","yellow","green"])',
    'z':'param.ObjectSelector(default="yellow", objects=["red","yellow","green"])',
    'colorbar':'param.ObjectSelector(default="yellow" ,objects=["red","yellow","green"])',
    'stacked':'param.Boolean(default=False)',
    'columns':'param.ObjectSelector(default="yellow", objects=["red","yellow","green"])',
    'where':'param.ObjectSelector(default="yellow", objects=["red","yellow","green"])',
    'width': 'param.Integer(default=800, bounds=(200,1600))',
    'height': 'param.Integer(default=600, bounds=(200,1600))',
        'shared_axes' : 'param.Boolean(True, doc="Share axes parameter")',
        'grid'        : 'param.Boolean(default=False, doc="Whether to show a grid")',
        'legend'      : 'param.ObjectSelector(default="top", objects=(None, "top", "bottom", "left", "right"), doc="Whether to show a legend, or a legend position")',
        'rot'         : 'param.Integer(default=45, bounds=(0,180), doc="Rotates the axis ticks along the x-axis by the specified number of degrees.")',
        'xlim'        : 'param.Number(8.2,bounds=(7.5,10))',
        'ylim'        : 'param.Number(8.2,bounds=(7.5,10))',
        'xticks'      : 'param.Integer(default=6,bounds=(1,10) )',
        'yticks'      : 'param.Integer(default=6,bounds=(1,10) )',
        'colorbar'    : 'param.Boolean(default=False, doc="Enables colorbar")',
        'invert'      : 'param.Boolean(default=False, doc="Swaps, x- y- Axis")',
        'title'       : 'param.String(default="")',
        'logx'        : 'param.Boolean(default=False,doc= "Enables logarithmic x-axis")',
        'logy'        : 'param.Boolean(default=False,doc=" Enables logarithmic y-axis")',
        'logz'        : 'param.Boolean(default=False,doc="Enables logarithmic z-axis")',
        'loglog'      : 'param.Boolean(default=False,doc="Enables logarithmic x- and y-axis")',
        'xaxis'       : 'param.ObjectSelector(default="bottom",objects=["top", "bottom", None])',
        'yaxis'       : 'param.ObjectSelector(default="left",objects=["left","right", None])',
        'xformatter'  : 'param.String(default="%3.f")',
        'yformatter'  : 'param.String(default="%3.f")',
        'xlabel'      : 'param.String(default="", doc="Axis labels for the x-axis")',
        'ylabel'      : 'param.String(default="", doc="Axis labels for the y-axis")',
        'padding'     : 'param.Range(default=(0, 10), bounds=(0,10))',

}

# Class Options

In [65]:
hv_class = df.hvplot
members = []
all_args_types = []
all_types = []
all_opts_types = []
common_opts = []
def intersection(lst1, lst2): 
    return list(set(lst1) & set(lst2)) 

def arg_to_widget_name(arg):
    try:
        return map_type_to_widget[arg]
    except Exception as e:
        return 'param.ObjectSelector(default="yellow",objects=["red","yellow","green"])'
    
for memb in inspect.getmembers(hv_class, predicate=inspect.ismethod):
    if '_' not in memb[0]:
        members.append(memb)

def print_class_options(args, class_name):
    my_class = class_name+'Panel'
    classOptionName = class_name.capitalize()+'PanelOptions'
    print('class '+my_class+'(param.Parameterized):\n')
    for arg in args:
        str_len = "#        {:<"+str(len(str(max(args, key=len)))+1)+"}= "+arg_to_widget_name(arg)
        print(str_len.format(arg))
    print('')
    print('        #######################')
    print('        # Optional parameters #')
    print('        #######################')
    print('#        options = param.Parameter(precedence=3)')
    # for opt in opts:
    #     str_len = "        # {:<"+str(len(str(max(opts, key=len)))+1)+"}= "+arg_to_widget_name(opt)
    #     print(str_len.format(opt))
          
    print('')
    print('        def __init__(self, dataframe=None, objects=None, defaults=None, **params):')
    print('#            if "options" not in params:')
    print('#                params["options"] = '+classOptionName+'(name="Options")')
    print('            if dataframe is not None:')
    print('                self.dataframe = dataframe')
    print('            else:')
    print('                self.dataframe = df')
    #print('            for k, v in objects.items():')
    #print('                try:')
    #print('                    self.param[k].objects = v')
    #print('                except:')
    #print('                    pass')
    #print('            for k, v in defaults.items():')
    #print('                try:')
    #print('                    setattr(self, k, v)')
    #print('                except:')
    #print('                    pass')   
    print('            self.set_options()\n')
    print('            super('+my_class+', self).__init__(**params)\n')
    
    print('        def set_options(self):')
    print('            self.plot_options = {')
    for arg in args:
        str_len = "#                {:<"+str(len(str(max(args, key=len)))+1)+"} : self."+arg+","
        print(str_len.format("'"+arg+"'"))
        
    # for opt in opts:
    #     str_len = "                # {:<"+str(len(str(max(opts, key=len)))+1)+"} : self."+opt+","
    #     print(str_len.format("'"+opt+"'"))
    print('            }\n')

    print('        def view(self):')
    print('            self.set_options()')
    print('            return self.plot_options')
    # print('            return self.dataframe.hvplot.'+name+'(**self.plot_options)\n')
    print(class_name.lower()+' = '+my_class+'(dataframe=df, objects=objects, defaults=defaults)')
    print('pn.Row('+class_name.lower()+', '+class_name.lower()+'.view)\n')
    
print_class_options(args=_axis_options, class_name='AxisOptions')

class AxisOptionsPanel(param.Parameterized):

#        width       = param.Integer(default=800, bounds=(200,1600))
#        height      = param.Integer(default=600, bounds=(200,1600))
#        shared_axes = param.Boolean(True, doc="Share axes parameter")
#        grid        = param.Boolean(default=False, doc="Whether to show a grid")
#        legend      = param.ObjectSelector(default="top", objects=(None, "top", "bottom", "left", "right"), doc="Whether to show a legend, or a legend position")
#        rot         = param.Integer(default=45, bounds=(0,180), doc="Rotates the axis ticks along the x-axis by the specified number of degrees.")
#        xlim        = param.Number(8.2,bounds=(7.5,10))
#        ylim        = param.Number(8.2,bounds=(7.5,10))
#        xticks      = param.Integer(default=6,bounds=(1,10) )
#        yticks      = param.Integer(default=6,bounds=(1,10) )
#        colorbar    = param.Boolean(default=False, doc="Enables colorbar")
#        invert      = param.Boolean

In [66]:
#%%writefile ../hvplot_panel/axis_options.py

class AxisOptionsPanel(param.Parameterized):

        width       = param.Integer(default=800, bounds=(200,1600))
        height      = param.Integer(default=600, bounds=(200,1600))
        shared_axes = param.Boolean(True, doc="Share axes parameter")
        grid        = param.Boolean(default=False, doc="Whether to show a grid")
        legend      = param.ObjectSelector(default="top", objects=(None, "top", "bottom", "left", "right"), doc="Whether to show a legend, or a legend position")
        rot         = param.Integer(default=45, bounds=(0,180), doc="Rotates the axis ticks along the x-axis by the specified number of degrees.")
#        xlim        = param.Number(8.2,bounds=(7.5,10))
#        ylim        = param.Number(8.2,bounds=(7.5,10))
        xticks      = param.Integer(default=6,bounds=(1,10) )
        yticks      = param.Integer(default=6,bounds=(1,10) )
        colorbar    = param.Boolean(default=False, doc="Enables colorbar")
        invert      = param.Boolean(default=False, doc="Swaps, x- y- Axis")
        title       = param.String(default="")
        logx        = param.Boolean(default=False,doc= "Enables logarithmic x-axis")
        logy        = param.Boolean(default=False,doc=" Enables logarithmic y-axis")
        loglog      = param.Boolean(default=False,doc="Enables logarithmic x- and y-axis")
        xaxis       = param.ObjectSelector(default="bottom",objects=["top", "bottom", None])
        yaxis       = param.ObjectSelector(default="left",objects=["left","right", None])
#        xformatter  = param.String(default="%3.f")
#        yformatter  = param.String(default="%3.f")
        xlabel      = param.String(default="", doc="Axis labels for the x-axis")
        ylabel      = param.String(default="", doc="Axis labels for the y-axis")
#        padding     = param.Range(default=(0, 10), bounds=(0,10))

        #######################
        # Optional parameters #
        #######################
#        options = param.Parameter(precedence=3)

        def __init__(self, dataframe=None, objects=None, defaults=None, **params):
#            if "options" not in params:
#                params["options"] = AxisoptionsPanelOptions(name="Options")
            if dataframe is not None:
                self.dataframe = dataframe
            else:
                self.dataframe = df
            self.set_options()

            super(AxisOptionsPanel, self).__init__(**params)

        def set_options(self):
            self.plot_options = {
                'width'      : self.width,
                'height'     : self.height,
                'shared_axes' : self.shared_axes,
                'grid'       : self.grid,
                'legend'     : self.legend,
                'rot'        : self.rot,
#                'xlim'       : self.xlim,
#                'ylim'       : self.ylim,
                'xticks'     : self.xticks,
                'yticks'     : self.yticks,
                'colorbar'   : self.colorbar,
                'invert'     : self.invert,
                'title'      : self.title,
                'logx'       : self.logx,
                'logy'       : self.logy,
                'loglog'     : self.loglog,
                'xaxis'      : self.xaxis,
                'yaxis'      : self.yaxis,
#                'xformatter' : self.xformatter,
#                'yformatter' : self.yformatter,
                'xlabel'     : self.xlabel,
                'ylabel'     : self.ylabel,
#                'padding'    : self.padding,
            }

        def view(self):
            self.set_options()
            return self.plot_options


In [67]:
        
axisoptions = AxisOptionsPanel(dataframe=df, objects=objects, defaults=defaults)
pn.Row(axisoptions, axisoptions.view)

Row
    [0] Column(margin=5, name='Param03052', width=300)
        [0] StaticText(value='<b>AxisOptionsPanel</b>')
        [1] IntSlider(end=1600, name='Width', start=200, value=800)
        [2] IntSlider(end=1600, name='Height', start=200, value=600)
        [3] Checkbox(name='Shared axes', value=True)
        [4] Checkbox(name='Grid')
        [5] Select(name='Legend', options=OrderedDict([('None', ...]), value='top')
        [6] IntSlider(end=180, name='Rot', value=45)
        [7] IntSlider(end=10, name='Xticks', start=1, value=6)
        [8] IntSlider(end=10, name='Yticks', start=1, value=6)
        [9] Checkbox(name='Colorbar')
        [10] Checkbox(name='Invert')
        [11] TextInput(name='Title')
        [12] Checkbox(name='Logx')
        [13] Checkbox(name='Logy')
        [14] Checkbox(name='Loglog')
        [15] Select(name='Xaxis', options=OrderedDict([('top', ...]), value='bottom')
        [16] Select(name='Yaxis', options=OrderedDict([('left', ...]), value='left')
        [17] TextInput(name='Xlabel')
        [18] TextInput(name='Ylabel')
    [1] ParamMethod(method)

# Class principale

In [68]:

        
def print_class(class_name, generic_opts=_axis_options):
    my_class = class_name.capitalize()+'Panel'
    args, opts = get_args(eval('hv_class.'+class_name))
    classOptionName = name.capitalize()+'AxisPanelOptions'
    print('class '+my_class+'(param.Parameterized):\n')
    for arg in args:
        str_len = "        {:<"+str(len(str(max(args, key=len)))+1)+"}= "+arg_to_widget_name(arg)
        print(str_len.format(arg))
    print('')
    print('        #######################')
    print('        # Optional parameters #')
    print('        #######################')
    print('        options_axis = param.Parameter(precedence=3)')
    # for opt in generic_opts:
    #     str_len = "        # {:<"+str(len(str(max(opts, key=len)))+1)+"}= "+arg_to_widget_name(opt)
    #     print(str_len.format(opt))
          
    print('')
    print('        def __init__(self, dataframe=None, objects=None, defaults=None, **params):')
    print('            if "options" not in params:')
    print('                params["options_axis"] = AxisOptionsPanel(name="Options")')
    print('            if dataframe is not None:')
    print('                self.dataframe = dataframe')
    print('            else:')
    print('                self.dataframe = df')
    print('            for k, v in objects.items():')
    print('                try:')
    print('                    self.param[k].objects = v')
    print('                except:')
    print('                    pass')
    print('            for k, v in defaults.items():')
    print('                try:')
    print('                    setattr(self, k, v)')
    print('                except:')
    print('                    pass')   
    print('            super('+my_class+', self).__init__(**params)\n')
    print('            self.set_options()\n')
    
    print('        def set_options(self):')
    print('            self.plot_options = {')
    for arg in args:
        str_len = "                {:<"+str(len(str(max(args, key=len)))+1)+"} : self."+arg+","
        print(str_len.format("'"+arg+"'"))
    
    print('        #######################')
    print('        # Generic opts param. #')
    print('        #######################')
    for opt in generic_opts:
        str_len = "                # {:<"+str(len(str(max(opts, key=len)))+1)+"} : self.options_axis."+opt+","
        print(str_len.format("'"+opt+"'"))
        
    
    print('            }\n')
    print('        @param.depends(')
    for arg in args:
        str_len = "               '"+arg+"',"
        print(str_len.format("'"+arg+"'"))
    for opt in generic_opts:
        str_len = "#               'options_axis."+opt+"',"
        print(str_len.format(","+opt+"'"))
    print('             watch=True)')

    print('        def view(self):')
    print('            self.set_options()')
    print('            return self.dataframe.hvplot.'+name+'(**self.plot_options)\n')
    print(name+' = '+my_class+'(dataframe=df, objects=objects, defaults=defaults)')
    print('pn.Row('+name+', '+name+'.view)\n')

for graph_type in members:
    name = graph_type[0]
    print_class(class_name=name, generic_opts=_axis_options)
    


class AreaPanel(param.Parameterized):

        x       = param.ObjectSelector(default="yellow", objects=["red","yellow","green"])
        y       = param.ListSelector(default=["yellow"], objects=["red","yellow","green"])
        y2      = param.ObjectSelector(default="yellow", objects=["red","yellow","green"])
        stacked = param.Boolean(default=False)

        #######################
        # Optional parameters #
        #######################
        options_axis = param.Parameter(precedence=3)

        def __init__(self, dataframe=None, objects=None, defaults=None, **params):
            if "options" not in params:
                params["options_axis"] = AxisOptionsPanel(name="Options")
            if dataframe is not None:
                self.dataframe = dataframe
            else:
                self.dataframe = df
            for k, v in objects.items():
                try:
                    self.param[k].objects = v
                except:
                    pass
 

In [69]:
class LinePanel(param.Parameterized):

        x = param.ObjectSelector(default="yellow", objects=["red","yellow","green"])
        y = param.ListSelector(default=["yellow"], objects=["red","yellow","green"])

        #######################
        # Optional parameters #
        #######################
        options_axis = param.Parameter(precedence=3)

        def __init__(self, dataframe=None, objects=None, defaults=None, **params):
            if "options" not in params:
                params["options_axis"] = AxisOptionsPanel(name="Options")
            if dataframe is not None:
                self.dataframe = dataframe
            else:
                self.dataframe = df
            for k, v in objects.items():
                try:
                    self.param[k].objects = v
                except:
                    pass
            for k, v in defaults.items():
                try:
                    setattr(self, k, v)
                except:
                    pass
            super(LinePanel, self).__init__(**params)

            self.set_options()

        def set_options(self):
            self.plot_options = {
                'x' : self.x,
                'y' : self.y,
        #######################
        # Generic opts param. #
        #######################
                 'width'                  : self.options_axis.width,
                 'height'                 : self.options_axis.height,
                 'shared_axes'            : self.options_axis.shared_axes,
                 'grid'                   : self.options_axis.grid,
                 'legend'                 : self.options_axis.legend,
                 'rot'                    : self.options_axis.rot,
                # 'xlim'                   : self.options_axis.xlim,
                # 'ylim'                   : self.options_axis.ylim,
#                 'xticks'                 : self.options_axis.xticks,
#                 'yticks'                 : self.options_axis.yticks,
                 'colorbar'               : self.options_axis.colorbar,
                 'invert'                 : self.options_axis.invert,
                 'title'                  : self.options_axis.title,
                 'logx'                   : self.options_axis.logx,
                 'logy'                   : self.options_axis.logy,
                 'loglog'                 : self.options_axis.loglog,
                 'xaxis'                  : self.options_axis.xaxis,
                 'yaxis'                  : self.options_axis.yaxis,
                # 'xformatter'             : self.options_axis.xformatter,
                # 'yformatter'             : self.options_axis.yformatter,
                 'xlabel'                 : self.options_axis.xlabel,
                 'ylabel'                 : self.options_axis.ylabel,
                # 'padding'                : self.options_axis.padding,
            }

        @param.depends(
               'x',
               'y',
               'options_axis.width',
               'options_axis.height',
               'options_axis.shared_axes',
               'options_axis.grid',
               'options_axis.legend',
               'options_axis.rot',
#               'options_axis.xlim',
#               'options_axis.ylim',
#               'options_axis.xticks',
#               'options_axis.yticks',
               'options_axis.colorbar',
               'options_axis.invert',
               'options_axis.title',
               'options_axis.logx',
               'options_axis.logy',
               'options_axis.loglog',
               'options_axis.xaxis',
               'options_axis.yaxis',
#               'options_axis.xformatter',
#               'options_axis.yformatter',
               'options_axis.xlabel',
               'options_axis.ylabel',
#               'options_axis.padding',
             watch=True)
        def view(self):
            self.set_options()
            return self.dataframe.hvplot.line(**self.plot_options)

line = LinePanel(dataframe=df, objects=objects, defaults=defaults)
pn.Row(line, line.view)


Row
    [0] Column(margin=5, name='Param03123', width=300)
        [0] StaticText(value='<b>LinePanel</b>')
        [1] Select(name='X', options=OrderedDict([('date', ...]), value='date')
        [2] MultiSelect(name='Y', options=OrderedDict([('date', ...]), value=['Temperature'])
        [3] Row(width_policy='max')
            [0] LiteralInput(margin=(5, 0, 5, 10), name='Options axis', value=AxisOptionsPanel(colorbar=..., width=240)
            [1] Toggle(align='center', button_type='primary', height_policy='fit', margin=(0, 0, 0, 10), max_height=30, max_width=20, name='⋮')
    [1] ParamMethod(method)

In [71]:
class AxisOptionsPanel(param.Parameterized):

        width       = param.Integer(default=800, bounds=(200,1600))
        height      = param.Integer(default=600, bounds=(200,1600))
        shared_axes = param.Boolean(True, doc="Share axes parameter")
        grid        = param.Boolean(default=False, doc="Whether to show a grid")
        legend      = param.ObjectSelector(default="top", objects=(None, "top", "bottom", "left", "right"), doc="Whether to show a legend, or a legend position")
        rot         = param.Integer(default=45, bounds=(0,180), doc="Rotates the axis ticks along the x-axis by the specified number of degrees.")
        # xlim        = param.Range(default=(0, 10), bounds=(0,10))
        # ylim        = param.Range(default=(0, 10), bounds=(0,10))
        xticks      = param.Integer(default=6,bounds=(1,10) )
        yticks      = param.Integer(default=6,bounds=(1,10) )
        colorbar    = param.Boolean(default=False, doc="Enables colorbar")
        invert      = param.Boolean(default=False, doc="Swaps, x- y- Axis")
        title       = param.String(default="")
        logx        = param.Boolean(default=False,doc= "Enables logarithmic x-axis")
        logy        = param.Boolean(default=False,doc=" Enables logarithmic y-axis")
        loglog      = param.Boolean(default=False,doc="Enables logarithmic x- and y-axis")
        xaxis       = param.ObjectSelector(default="bottom",objects=["top", "bottom", None])
        yaxis       = param.ObjectSelector(default="left",objects=["left","right", None])
        # xformatter  = param.String(default="%3.f")
        # yformatter  = param.String(default="%3.f")
        xlabel      = param.String(default="", doc="Axis labels for the x-axis")
        ylabel      = param.String(default="", doc="Axis labels for the y-axis")
        # padding     = param.Range(default=(0, 10), bounds=(0,10))


        #######################
        # Optional parameters #
        #######################
#        options = param.Parameter(precedence=3)

        def __init__(self, dataframe=None, objects=None, defaults=None, **params):
#            if "options" not in params:
#                params["options"] = AxisoptionsPanelOptions(name="Options")
            if dataframe is not None:
                self.dataframe = dataframe
            else:
                self.dataframe = df
            self.set_options()

            super(AxisOptionsPanel, self).__init__(**params)

        def set_options(self):
            self.plot_options = {
                'width'      : self.width,
                'height'     : self.height,
                'shared_axes' : self.shared_axes,
                'grid'       : self.grid,
                'legend'     : self.legend,
                'rot'        : self.rot,
                # 'xlim'       : self.xlim,
                # 'ylim'       : self.ylim,
                'xticks'     : self.xticks,
                'yticks'     : self.yticks,
                'colorbar'   : self.colorbar,
                'invert'     : self.invert,
                'title'      : self.title,
                'logx'       : self.logx,
                'logy'       : self.logy,
                'loglog'     : self.loglog,
                'xaxis'      : self.xaxis,
                'yaxis'      : self.yaxis,
                # 'xformatter' : self.xformatter,
                # 'yformatter' : self.yformatter,
                'xlabel'     : self.xlabel,
                'ylabel'     : self.ylabel,
                # 'padding'    : self.padding,
            }

        def view(self):
            self.set_options()
            return self.plot_options
        
axisoptions = AxisOptionsPanel(dataframe=df, objects=objects, defaults=defaults)
pn.Row(axisoptions, axisoptions.view)

Row
    [0] Column(margin=5, name='Param03380', width=300)
        [0] StaticText(value='<b>AxisOptionsPanel</b>')
        [1] IntSlider(end=1600, name='Width', start=200, value=800)
        [2] IntSlider(end=1600, name='Height', start=200, value=600)
        [3] Checkbox(name='Shared axes', value=True)
        [4] Checkbox(name='Grid')
        [5] Select(name='Legend', options=OrderedDict([('None', ...]), value='top')
        [6] IntSlider(end=180, name='Rot', value=45)
        [7] IntSlider(end=10, name='Xticks', start=1, value=6)
        [8] IntSlider(end=10, name='Yticks', start=1, value=6)
        [9] Checkbox(name='Colorbar')
        [10] Checkbox(name='Invert')
        [11] TextInput(name='Title')
        [12] Checkbox(name='Logx')
        [13] Checkbox(name='Logy')
        [14] Checkbox(name='Loglog')
        [15] Select(name='Xaxis', options=OrderedDict([('top', ...]), value='bottom')
        [16] Select(name='Yaxis', options=OrderedDict([('left', ...]), value='left')
        [17] TextInput(name='Xlabel')
        [18] TextInput(name='Ylabel')
    [1] ParamMethod(method)

In [76]:
line = LinePanel(dataframe=df, objects=objects, defaults=defaults)

subpanel = pn.Column()
pn.Row(
   pn.Column(pn.Param(line.param, expand_layout=subpanel), subpanel), line.view
)
#pn.Column(pn.Row(line, line.view))

Row
    [0] Column
        [0] Param(LinePanel, expand_layout=Column())
        [1] Column()
    [1] ParamMethod(method)